## Librairies needed to execute this notebook

In [10]:
try:
    import json
    import codecs
    import pyodbc 
    from tqdm.notebook import tqdm
    print("Librairies Loaded")
    
except Exception as e:
    print("Error, missing librairies : {} ".format(e))

Librairies Loaded


### 1. Downloading quran with chakl

In [2]:
# instated of using the json her, you can build your own json file or at least use an offline file 
!curl https://raw.githubusercontent.com/risan/quran-json/master/json/quran/text.pretty.json > surat.json
!curl https://raw.githubusercontent.com/risan/quran-json/master/json/surahs.pretty.json > ayat.json

  % Total    % Received % Xferd  Average Speed   Time    Time     Time  Current
                                 Dload  Upload   Total   Spent    Left  Speed

  0     0    0     0    0     0      0      0 --:--:-- --:--:-- --:--:--     0
  0     0    0     0    0     0      0      0 --:--:-- --:--:-- --:--:--     0
  9 1751k    9  168k    0     0   123k      0  0:00:14  0:00:01  0:00:13  123k
 37 1751k   37  655k    0     0   277k      0  0:00:06  0:00:02  0:00:04  277k
 64 1751k   64 1137k    0     0   338k      0  0:00:05  0:00:03  0:00:02  338k
 93 1751k   93 1629k    0     0   373k      0  0:00:04  0:00:04 --:--:--  373k
100 1751k  100 1751k    0     0   380k      0  0:00:04  0:00:04 --:--:--  429k
  % Total    % Received % Xferd  Average Speed   Time    Time     Time  Current
                                 Dload  Upload   Total   Spent    Left  Speed

  0     0    0     0    0     0      0      0 --:--:-- --:--:-- --:--:--     0
100 22365  100 22365    0     0  40080      0 --:-

In [11]:
# reading documents with the utf-8-sig paramter to decode arabic characters 
surat = codecs.open('ayat_G2.json', 'r', 'utf-8-sig')
ayat = codecs.open('surat_G2.json', 'r', 'utf-8-sig')

json_surat = json.load(surat)
json_ayat = json.load(ayat)

# testing loaded data
json_ayat[7]

{'surah_number': 2,
 'verse_number': 1,
 'content': 'بِسْمِ ٱللَّهِ ٱلرَّحْمَٰنِ ٱلرَّحِيمِ الٓمٓ'}

In [12]:
# testing loaded surat
json_surat[0]

{'number': 1,
 'name': 'سورة الفاتحة',
 'transliteration_en': 'Al-Faatiha',
 'translation_en': 'The Opening',
 'total_verses': 7,
 'revelation_type': 'Meccan'}

### 2. Reading quran without chakl

In [13]:
repo = 'C:/Users/Houssam/Desktop/pfa/Projet ELK/'
no_chakl = codecs.open(repo+'codebeautify_G2.json', 'r', 'utf-8-sig') #Change to your path
json_no_chakl = json.load(no_chakl)
json_no_chakl[7]

{'index': '8', 'sura': '2', 'aya': '1', 'text': 'بسم الله الرحمن الرحيم الم'}

### 3. Reading tafsir from SQL Server

In [14]:
# Connect to an SQL server instance and use the database quran containing tafssir 
conn = pyodbc.connect('Driver={ODBC Driver 13 for SQL Server};'
                      'Server=STARGAZER111;' #change this to the name of your server (DESKTOP-XXXXXX)
                      'Database=quran;'
                      'Trusted_Connection=yes;')

cursor = conn.cursor()

In [15]:
# retrieving tafsir
cursor.execute('SELECT * FROM dbo.tafsir1')
c = 7               #set it to the index of aya to get the tafsir associated
for row in cursor:
    print(" aya_index_quran: ", row[0], "\n sura_index: ", row[1], "\n aya_index_sura: ", row[2], "\n tafsir:\n ", row[3])
    break

 aya_index_quran:  1 
 sura_index:  1 
 aya_index_sura:  1 
 tafsir:
  ( بسم الله الرحمن الرحيم ) بسم الله الباء أداة تخفض ما بعدها مثل من وعن والمتعلق به الباء محذوف لدلالة الكلام عليه تقديره أبدأ بسم الله أو قل بسم الله . وأسقطت الألف من الاسم طلبا للخفة وكثرة استعمالها وطولت الباء قال القتيبي ليكون افتتاح كلام كتاب الله بحرف معظم كان عمر بن عبد العزيز رحمه الله يقول لكتابه طولوا الباء وأظهروا السين وفرجوا بينهما ودوروا الميم . تعظيما لكتاب الله تعالى وقيل لما أسقطوا الألف ردوا طول الألف على الباء ليكون دالا على سقوط الألف ألا ترى أنه لما كتبت الألف في " اقرأ باسم ربك " ( 1 - العلق ) ردت الباء إلى صيغتها ولا تحذف الألف إذا أضيف الاسم إلى غير الله ولا مع غير الباء .والاسم هو المسمى وعينه وذاته قال الله تعالى : " إنا نبشرك بغلام اسمه يحيى " ( 7 - مريم ) أخبر أن اسمه يحيى ثم نادى الاسم فقال : يا يحيى " وقال : ما تعبدون من دونه إلا أسماء سميتموها " ( 40 - يوسف ) وأراد الأشخاص المعبودة لأنهم كانوا يعبدون المسميات وقال : سبح اسم ربك " ( 1 - الأعلى ) ، وتبارك اسم ربك " ثم يقال للتسمية أيضا 

### 4. Generate our list of documents > quran (list of ayat)

In [16]:
# you can improuve your mapping to add a fields related to taffsir. assuming each aya has tafssir row
quran = []

cursor.execute('SELECT * FROM dbo.tafsir1')
for row in cursor:
    quran.append({
        "aya_index_quran": row[0],
        "aya_index_sura": row[2],
        "sura_name": json_surat[row[1]-1]['name'],
        "sura_index": row[1],
        "total_verses": json_surat[row[1]-1]['total_verses'],
        "aya_chakl": json_ayat[row[0]-1]['content'],
        "aya_no_chakl": json_no_chakl[row[0]-1]['text'],
        "tafsir_aya": row[3],
    })
#Ok this is nice
print(quran[0])

{'aya_index_quran': 1, 'aya_index_sura': 1, 'sura_name': 'سورة الفاتحة', 'sura_index': 1, 'total_verses': 7, 'aya_chakl': 'بِسْمِ ٱللَّهِ ٱلرَّحْمَٰنِ ٱلرَّحِيمِ', 'aya_no_chakl': 'بسم الله الرحمن الرحيم', 'tafsir_aya': '( بسم الله الرحمن الرحيم ) بسم الله الباء أداة تخفض ما بعدها مثل من وعن والمتعلق به الباء محذوف لدلالة الكلام عليه تقديره أبدأ بسم الله أو قل بسم الله . وأسقطت الألف من الاسم طلبا للخفة وكثرة استعمالها وطولت الباء قال القتيبي ليكون افتتاح كلام كتاب الله بحرف معظم كان عمر بن عبد العزيز رحمه الله يقول لكتابه طولوا الباء وأظهروا السين وفرجوا بينهما ودوروا الميم . تعظيما لكتاب الله تعالى وقيل لما أسقطوا الألف ردوا طول الألف على الباء ليكون دالا على سقوط الألف ألا ترى أنه لما كتبت الألف في " اقرأ باسم ربك " ( 1 - العلق ) ردت الباء إلى صيغتها ولا تحذف الألف إذا أضيف الاسم إلى غير الله ولا مع غير الباء .والاسم هو المسمى وعينه وذاته قال الله تعالى : " إنا نبشرك بغلام اسمه يحيى " ( 7 - مريم ) أخبر أن اسمه يحيى ثم نادى الاسم فقال : يا يحيى " وقال : ما تعبدون من دونه إلا أسماء سم

### 5. Insert data into ELK

In [49]:
from elasticsearch import Elasticsearch

es = Elasticsearch([{'host': 'localhost', 'port': '9200'}])
es.ping()

True

In [11]:
# creatting the indexe
es.indices.create(index="quran_g2",ignore=400)

{'acknowledged': True, 'shards_acknowledged': True, 'index': 'quran_g2'}

In [20]:
#Setting the mapping
mapping = {
    "settings": {
        "number_of_shards": 2,
        "number_of_replicas": 1
    },
    "mappings": {
    "properties" : {
        "aya_chakl" : {
          "type" : "text",
          "fields" : {
            "keyword" : {
              "type" : "keyword",
              "ignore_above" : 256
            }
          }
        },
        "aya_index_quran" : {
          "type" : "long"
        },
        "aya_index_sura" : {
          "type" : "long"
        },
        
        "aya_no_chakl":   { "type" : "text", "analyzer" : "arabic", "fielddata" : "true" },
        
        "sura_index" : {
          "type" : "long"
        },
        "sura_name" : {
          "type" : "text",
          "fields" : {
            "keyword" : {
              "type" : "keyword",
              "ignore_above" : 256
            }
          }
        },
        "tafsir_aya" : {
          "type" : "text",
          "fields" : {
            "keyword" : {
              "type" : "keyword",
              "ignore_above" : 256
            }
          }
        },
        "total_verses" : {
          "type" : "long"
        }
      }
    }
}

In [62]:
mapping1 = {
    "settings" : {
       "number_of_shards":2,
       "number_of_replicas":1,

    "analysis":{
   "filter":{
      "arabic_stop":{
         "type":"stop",
         "stopwords_path":"D:/Elastic/elasticsearch/config/merged-stopwords.txt"
      },
      "arabic_keywords":{
         "type":"keyword_marker",
         "keywords_path":"D:/Elastic/elasticsearch/config/keywordmarker-words.txt"
      },
      "arabic_stemmer":{
         "type":"stemmer",
         "language":"arabic"
      },
      "arabic_shingle":{
         "type":"shingle",
         "min_shingle_size":2,
         "max_shingle_size":3
      }
   },
   "analyzer":{
      "rebuilt_arabic":{
         "tokenizer":"standard",
         "filter":[
            "arabic_stop",
            "arabic_normalization",
            "arabic_keywords",
            "arabic_shingle",
            "arabic_stemmer"
         ]
      },
       "rebuilt":{
         "tokenizer":"standard",
         "filter":[
            "arabic_stop",
            "arabic_normalization",
            "arabic_keywords",
            "arabic_stemmer"
         ]
      },
      "simple_arabic":{
         "tokenizer":"standard",
         "filter":[
            "arabic_stop",
            "arabic_normalization",
            "arabic_shingle"
         ]
      },
      "noshingle_arabic": {
          "tokenizer":"standard",
         "filter":[
            "arabic_stop",
            "arabic_normalization"
         ]
      }
   }
}
    },
"mappings":{
   "properties":{
      "aya_chakl":{
         "type":"text",
         "fields":{
            "keyword":{
               "type":"keyword",
               "ignore_above":256
            }
         }
      },
      "aya_index_quran":{
         "type":"long"
      },
      "aya_index_sura":{
         "type":"long"
      },
      "aya_no_chakl":{
         "type":"text",
         "analyzer":"rebuilt_arabic",
         "fielddata":"true",
         "term_vector" : "yes",
         "fields":{
            "nostem":{
               "type":"text",
               "analyzer":"simple_arabic",
               "fielddata":"true",
               "term_vector" : "yes"
            },
             "noshingle":{
               "type":"text",
               "analyzer":"noshingle_arabic",
               "fielddata":"true",
               "term_vector" : "yes"
             },
             "stem_noshingle":{
               "type":"text",
               "analyzer":"rebuilt",
               "fielddata":"true",
               "term_vector" : "yes"
             },
            "keyword":{
               "type":"keyword"
            }
         }
      },
      "sura_index":{
         "type":"long"
      },
      "sura_name":{
         "type":"text",
         "fields":{
            "keyword":{
               "type":"keyword",
               "ignore_above":256
            }
         }
      },
      "tafsir_aya":{
         "type":"text"
      },
      "total_verses":{
         "type":"long"
      }
   }
}
}
        

In [63]:
es.indices.create(index="quran2_g2", body=mapping1 )

{'acknowledged': True, 'shards_acknowledged': True, 'index': 'quran2_g2'}

In [60]:
es.indices.delete(index="quran2_g2" )

{'acknowledged': True}

In [64]:
es.reindex({"source": {"index": "quran_g2"},"dest": {"index": "quran2_g2"}}, wait_for_completion=True, request_timeout=300)

{'took': 33413,
 'timed_out': False,
 'total': 6235,
 'updated': 0,
 'created': 6235,
 'deleted': 0,
 'batches': 7,
 'version_conflicts': 0,
 'noops': 0,
 'retries': {'bulk': 0, 'search': 0},
 'throttled_millis': 0,
 'requests_per_second': -1.0,
 'throttled_until_millis': 0,
 'failures': []}

In [14]:
# verify the creation of the index showing all indices in EL
res= es.indices.get_alias("*")
for nomindex in res:
    print(nomindex)

.kibana-event-log-7.12.0-000001
quran1_g2
.kibana_task_manager_7.12.0_001
.kibana_7.12.0_001
.apm-custom-link
.ds-ilm-history-5-2021.04.08-000001
nobellaureates
quran_g2
nobelprizes
quran2_g2
.apm-agent-configuration
.tasks


D:\Anaconda3\lib\site-packages\elasticsearch\connection\base.py:200: ElasticsearchWarning: this request accesses system indices: [.kibana_task_manager_7.12.0_001, .kibana_7.12.0_001, .apm-custom-link, .apm-agent-configuration, .tasks], but in a future major version, direct access to system indices will be prevented by default
  warnings.warn(message, category=ElasticsearchWarning)


In [17]:
for obj in quran:
    es.index(index='quran2_g2', ignore=400, body=mapping1)

# Creating and reindexing to the new and final index with the specified mapping

In [17]:
es.indices.create(index="quran1_g2",body=mapping, ignore=400)

{'acknowledged': True, 'shards_acknowledged': True, 'index': 'quran1_g2'}

In [19]:
es.reindex({"source": {"index": "quran_g2"},"dest": {"index": "quran1_g2"}}, wait_for_completion=True, request_timeout=300)

{'took': 2527,
 'timed_out': False,
 'total': 6235,
 'updated': 0,
 'created': 6235,
 'deleted': 0,
 'batches': 7,
 'version_conflicts': 0,
 'noops': 0,
 'retries': {'bulk': 0, 'search': 0},
 'throttled_millis': 0,
 'requests_per_second': -1.0,
 'throttled_until_millis': 0,
 'failures': []}

# 6. Get docs by words of aya no chakl

# Question 1

In [ ]:
#جنة

In [36]:
query_body = {
  "size":1000,
  "query": {
    "match": {
      "aya_no_chakl.exact": {
        "query":"جنة"
      }
    }
  }
}

In [37]:
es.search(index="quran2_g2", body=query_body)

{'took': 64,
 'timed_out': False,
 '_shards': {'total': 2, 'successful': 2, 'skipped': 0, 'failed': 0},
 'hits': {'total': {'value': 18, 'relation': 'eq'},
  'max_score': 9.701896,
  'hits': [{'_index': 'quran2_g2',
    '_type': '_doc',
    '_id': 'yZW7EnkBH5h4-fN0AZqU',
    '_score': 9.701896,
    '_source': {'aya_index_quran': 4799,
     'aya_index_sura': 15,
     'sura_name': 'سورة النجم',
     'sura_index': 53,
     'total_verses': 62,
     'aya_chakl': 'عِندَهَا جَنَّةُ ٱلْمَأْوَىٰٓ',
     'aya_no_chakl': 'عندها جنة المأوى',
     'tafsir_aya': '( عندها جنة المأوى ) قال عطاء عن ابن عباس : جنة يأوي إليها جبريل والملائكة . وقال مقاتل والكلبي : يأوي إليها أرواح الشهداء .'}},
   {'_index': 'quran2_g2',
    '_type': '_doc',
    '_id': '65W7EnkBH5h4-fN0s5xw',
    '_score': 9.701896,
    '_source': {'aya_index_quran': 5345,
     'aya_index_sura': 22,
     'sura_name': 'سورة الحاقة',
     'sura_index': 69,
     'total_verses': 52,
     'aya_chakl': 'فِى جَنَّةٍ عَالِيَةٍ',
     'aya_no_cha

In [ ]:
# المتقون

In [31]:
query_body = {
  "size":1000,
  "query": {
    "match": {
      "aya_no_chakl.keyword": {
        "query":"المتقون"
      }
    }
  }
}

In [37]:
es.search(index="quran2_g2", body=query_body)

{'took': 137,
 'timed_out': False,
 '_shards': {'total': 1, 'successful': 1, 'skipped': 0, 'failed': 0},
 'hits': {'total': {'value': 49, 'relation': 'eq'},
  'max_score': 7.596263,
  'hits': [{'_index': 'quran2_g2',
    '_type': '_doc',
    '_id': '2JW4EnkBH5h4-fN0oZMB',
    '_score': 7.596263,
    '_source': {'aya_index_quran': 3022,
     'aya_index_sura': 90,
     'sura_name': 'سورة الشعراء',
     'sura_index': 26,
     'total_verses': 227,
     'aya_chakl': 'وَأُزْلِفَتِ ٱلْجَنَّةُ لِلْمُتَّقِينَ',
     'aya_no_chakl': 'وأزلفت الجنة للمتقين',
     'tafsir_aya': '( وأزلفت ) قربت  ( الجنة للمتقين )'}},
   {'_index': 'quran2_g2',
    '_type': '_doc',
    '_id': 'P5W6EnkBH5h4-fN01ZoI',
    '_score': 7.596263,
    '_source': {'aya_index_quran': 4661,
     'aya_index_sura': 31,
     'sura_name': 'سورة ق',
     'sura_index': 50,
     'total_verses': 45,
     'aya_chakl': 'وَأُزْلِفَتِ ٱلْجَنَّةُ لِلْمُتَّقِينَ غَيْرَ بَعِيدٍ',
     'aya_no_chakl': 'وأزلفت الجنة للمتقين غير بعيد',
     'ta

In [38]:
query_body = {
  "size":1000,
  "query": {
    "match": {
      "aya_no_chakl": {
        "query":"المؤمنون"
      }
    }
  }
}

In [41]:
 es.search(index="quran2_g2", body=query_body)

{'took': 300,
 'timed_out': False,
 '_shards': {'total': 1, 'successful': 1, 'skipped': 0, 'failed': 0},
 'hits': {'total': {'value': 185, 'relation': 'eq'},
  'max_score': 5.7244263,
  'hits': [{'_index': 'quran2_g2',
    '_type': '_doc',
    '_id': '_ZW4EnkBH5h4-fN0UJKX',
    '_score': 5.7244263,
    '_source': {'aya_index_quran': 2803,
     'aya_index_sura': 12,
     'sura_name': 'سورة النور',
     'sura_index': 24,
     'total_verses': 64,
     'aya_chakl': 'لَّوْلَآ إِذْ سَمِعْتُمُوهُ ظَنَّ ٱلْمُؤْمِنُونَ وَٱلْمُؤْمِنَٰتُ بِأَنفُسِهِمْ خَيْرًا وَقَالُوا۟ هَٰذَآ إِفْكٌ مُّبِينٌ',
     'aya_no_chakl': 'لولا إذ سمعتموه ظن المؤمنون والمؤمنات بأنفسهم خيرا وقالوا هذا إفك مبين',
     'tafsir_aya': 'قوله - عز وجل - : ( لولا ) هلا ( إذ سمعتموه ظن المؤمنون والمؤمنات بأنفسهم ) بإخوانهم ( خيرا ) قال الحسن : بأهل دينهم لأن المؤمنين كنفس واحدة ، نظيره قوله تعالى : ولا تقتلوا أنفسكم ( النساء - 29 ) فسلموا على أنفسكم ( النور - 61 ) . ( وقالوا هذا إفك مبين ) أي كذب بين .'}},
   {'_index': 'quran

In [64]:
query_body = {
  "size":1000,
  "query": {
    "match": {
      "aya_no_chakl": {
        "query":"الكافرون"
      }
    }
  }
}

In [65]:
es.search(index="quran_G2", body=query_body)

{'took': 82,
 'timed_out': False,
 '_shards': {'total': 1, 'successful': 1, 'skipped': 0, 'failed': 0},
 'hits': {'total': {'value': 17, 'relation': 'eq'},
  'max_score': 7.173242,
  'hits': [{'_index': 'quran',
    '_type': 'quran',
    '_id': 'Qa1TFncBarqUGLZS5QHh',
    '_score': 7.173242,
    '_source': {'aya_index_quran': 1984,
     'aya_index_sura': 83,
     'sura_name': 'سورة النحل',
     'sura_index': 16,
     'total_verses': 128,
     'aya_chakl': 'يَعْرِفُونَ نِعْمَتَ ٱللَّهِ ثُمَّ يُنكِرُونَهَا وَأَكْثَرُهُمُ ٱلْكَٰفِرُونَ',
     'aya_no_chakl': 'يعرفون نعمت الله ثم ينكرونها وأكثرهم الكافرون',
     'tafsir_aya': '( يعرفون نعمة الله ) قال السدي يعني : محمدا صلى الله عليه وسلم ، ( ثم ينكرونها ) يكذبون به .وقال قوم : هي الإسلام .وقال مجاهد ، وقتادة : يعني ما عد لهم من النعم في هذه السورة ، يقرون أنها من الله ، ثم إذا قيل لهم : تصدقوا وامتثلوا أمر الله فيها ، ينكرونها فيقولون : ورثناها من آبائنا .وقال الكلبي : هو أنه لما ذكر لهم هذه النعم قالوا : نعم ، هذه كلها من الله ، ولكنها ب

In [66]:
query_body = {
  "size":1000,
  "query": {
    "match": {
      "aya_no_chakl": {
        "query":"الفاسقون"
      }
    }
  }
}

In [67]:
es.search(index="quran_G2", body=query_body)

{'took': 4,
 'timed_out': False,
 '_shards': {'total': 1, 'successful': 1, 'skipped': 0, 'failed': 0},
 'hits': {'total': {'value': 9, 'relation': 'eq'},
  'max_score': 7.9190354,
  'hits': [{'_index': 'quran',
    '_type': 'quran',
    '_id': '-axPFncBarqUGLZSNfrR',
    '_score': 7.9190354,
    '_source': {'aya_index_quran': 375,
     'aya_index_sura': 82,
     'sura_name': 'سورة آل عمران',
     'sura_index': 3,
     'total_verses': 200,
     'aya_chakl': 'فَمَن تَوَلَّىٰ بَعْدَ ذَٰلِكَ فَأُو۟لَٰٓئِكَ هُمُ ٱلْفَٰسِقُونَ',
     'aya_no_chakl': 'فمن تولى بعد ذلك فأولئك هم الفاسقون',
     'tafsir_aya': '( فمن تولى بعد ذلك ) الإقرار ، ( فأولئك هم الفاسقون ) العاصون الخارجون عن الإيمان .'}},
   {'_index': 'quran',
    '_type': 'quran',
    '_id': '7KxOFncBarqUGLZSgPlO',
    '_score': 7.074294,
    '_source': {'aya_index_quran': 106,
     'aya_index_sura': 99,
     'sura_name': 'سورة البقرة',
     'sura_index': 2,
     'total_verses': 286,
     'aya_chakl': 'وَلَقَدْ أَنزَلْنَآ إِلَيْكَ ءَ

In [44]:
query_body = {
  "size":1000,
  "query": {
    "match": {
      "aya_no_chakl": {
        "query":"يصلح"
      }
    }
  }
}

In [45]:
es.search(index="quran2_g2", body=query_body)

{'took': 50,
 'timed_out': False,
 '_shards': {'total': 2, 'successful': 2, 'skipped': 0, 'failed': 0},
 'hits': {'total': {'value': 5, 'relation': 'eq'},
  'max_score': 10.325182,
  'hits': [{'_index': 'quran2_g2',
    '_type': '_doc',
    '_id': '0JW6EnkBH5h4-fN0sJnP',
    '_score': 10.325182,
    '_source': {'aya_index_quran': 4550,
     'aya_index_sura': 5,
     'sura_name': 'سورة محمد',
     'sura_index': 47,
     'total_verses': 38,
     'aya_chakl': 'سَيَهْدِيهِمْ وَيُصْلِحُ بَالَهُمْ',
     'aya_no_chakl': 'سيهديهم ويصلح بالهم',
     'tafsir_aya': '( سيهديهم ) أيام حياتهم في الدنيا إلى أرشد الأمور ، وفي الآخرة إلى الدرجات ( ويصلح بالهم ) يرضي خصماءهم ويقبل أعمالهم .'}},
   {'_index': 'quran2_g2',
    '_type': '_doc',
    '_id': 'FpW4EnkBH5h4-fN0vJRN',
    '_score': 9.663382,
    '_source': {'aya_index_quran': 3084,
     'aya_index_sura': 152,
     'sura_name': 'سورة الشعراء',
     'sura_index': 26,
     'total_verses': 227,
     'aya_chakl': 'ٱلَّذِينَ يُفْسِدُونَ فِى ٱلْأَرْضِ

In [46]:
query_body = {
  "size":1000,
  "query": {
    "match": {
      "aya_no_chakl": {
        "query":"مدرارا"
      }
    }
  }
}

In [47]:
es.search(index="quran2_g2", body=query_body)

{'took': 33,
 'timed_out': False,
 '_shards': {'total': 2, 'successful': 2, 'skipped': 0, 'failed': 0},
 'hits': {'total': {'value': 3, 'relation': 'eq'},
  'max_score': 10.432739,
  'hits': [{'_index': 'quran2_g2',
    '_type': '_doc',
    '_id': 'QJW7EnkBH5h4-fN0zJ1i',
    '_score': 10.432739,
    '_source': {'aya_index_quran': 5430,
     'aya_index_sura': 11,
     'sura_name': 'سورة نوح',
     'sura_index': 71,
     'total_verses': 28,
     'aya_chakl': 'يُرْسِلِ ٱلسَّمَآءَ عَلَيْكُم مِّدْرَارًا',
     'aya_no_chakl': 'يرسل السماء عليكم مدرارا',
     'tafsir_aya': '( يرسل السماء عليكم مدرارا ) وذلك أن قوم نوح لما كذبوه زمانا طويلا حبس الله عنهم المطر وأعقم أرحام نسائهم أربعين سنة ، فهلكت أموالهم ومواشيهم ، فقال لهم نوح : استغفروا ربكم من الشرك ، أي استدعوا المغفرة بالتوحيد ، يرسل السماء عليكم مدرارا .وروى مطرف عن الشعبي أن عمر رضي الله تعالى عنه خرج يستسقي بالناس ، فلم يزد على الاستغفار حتى رجع ، فقيل له : ما سمعناك استسقيت ؟ فقال . طلبت الغيث [ بمجاديح ] السماء التي يستنزل بها الم

In [52]:
query_body = {
  "size":1000,
  "query": {
    "match": {
      "aya_no_chakl": {
        "query":"فألهمها فجورها وتقواها "
      }
    }
  }
}

In [53]:
es.search(index="quran2_g2", body=query_body)

{'took': 51,
 'timed_out': False,
 '_shards': {'total': 2, 'successful': 2, 'skipped': 0, 'failed': 0},
 'hits': {'total': {'value': 3, 'relation': 'eq'},
  'max_score': 40.834084,
  'hits': [{'_index': 'quran2_g2',
    '_type': '_doc',
    '_id': 'rZW8EnkBH5h4-fN0i5_9',
    '_score': 40.834084,
    '_source': {'aya_index_quran': 6051,
     'aya_index_sura': 8,
     'sura_name': 'سورة الشمس',
     'sura_index': 91,
     'total_verses': 15,
     'aya_chakl': 'فَأَلْهَمَهَا فُجُورَهَا وَتَقْوَىٰهَا',
     'aya_no_chakl': 'فألهمها فجورها وتقواها',
     'tafsir_aya': '( فألهمها فجورها وتقواها ) قال ابن عباس في رواية علي بن أبي طلحة : بين لها الخير والشر . وقال في رواية عطية : علمها الطاعة والمعصية ، وروى الكلبي عن أبي صالح عنه : عرفها ما تأتي من الخير وما تتقي [ من الشر ] .وقال سعيد بن جبير : ألزمها فجورها وتقواها . قال ابن زيد : جعل فيها ذلك ، يعني بتوفيقه إياها للتقوى ، وخذلانه إياها للفجور . واختار الزجاج هذا ، وحمل الإلهام على التوفيق والخذلان ، وهذا يبين أن الله - عز وجل - خلق في المؤ

In [57]:
query_body = {
  "size":100,
  "query": {
    "bool": {
      "should": [{
        "query_string": {
            "query" :"aya_no_chakl.exact:' (والعصر OR والفجر OR فوربك OR أقسم)'"
        }}
      ]
    }
  }
}

In [58]:
es.search(index="quran2_g2", body=query_body)

{'took': 275,
 'timed_out': False,
 '_shards': {'total': 2, 'successful': 2, 'skipped': 0, 'failed': 0},
 'hits': {'total': {'value': 69, 'relation': 'eq'},
  'max_score': 19.721764,
  'hits': [{'_index': 'quran2_g2',
    '_type': '_doc',
    '_id': 'K5W8EnkBH5h4-fN0taAA',
    '_score': 19.721764,
    '_source': {'aya_index_quran': 6177,
     'aya_index_sura': 1,
     'sura_name': 'سورة العصر',
     'sura_index': 103,
     'total_verses': 3,
     'aya_chakl': 'بِسْمِ ٱللَّهِ ٱلرَّحْمَٰنِ ٱلرَّحِيمِ وَٱلْعَصْرِ',
     'aya_no_chakl': 'بسم الله الرحمن الرحيم والعصر',
     'tafsir_aya': 'مكية( والعصر ) قال ابن عباس : والدهر . قيل : أقسم به لأن فيه عبرة للناظر . وقيل : معناه ورب العصر ، وكذلك في أمثاله . وقال ابن كيسان : أراد بالعصر الليل والنهار ، يقال لهما العصران . وقال الحسن : من بعد زوال الشمس إلى غروبها . وقال قتادة : آخر ساعة من ساعات النهار . وقال مقاتل : أقسم بصلاة العصر وهي الصلاة الوسطى .'}},
   {'_index': 'quran2_g2',
    '_type': '_doc',
    '_id': 'dJW8EnkBH5h4-fN0eJ-Q',
    

# Question 2

In [8]:
query_body = {
  "size":1000,
  "query": {
    "match": {
      "aya_no_chakl": {
        "query":"المتقون"
      }
    }
  }
}

In [9]:
es.search(index="quran_G2", body=query_body)

{'took': 358,
 'timed_out': False,
 '_shards': {'total': 1, 'successful': 1, 'skipped': 0, 'failed': 0},
 'hits': {'total': {'value': 6, 'relation': 'eq'},
  'max_score': 8.061441,
  'hits': [{'_index': 'quran',
    '_type': 'quran',
    '_id': 'fK1aFncBarqUGLZS0wl0',
    '_score': 8.061441,
    '_source': {'aya_index_quran': 4091,
     'aya_index_sura': 33,
     'sura_name': 'سورة الزمر',
     'sura_index': 39,
     'total_verses': 75,
     'aya_chakl': 'وَٱلَّذِى جَآءَ بِٱلصِّدْقِ وَصَدَّقَ بِهِۦٓ أُو۟لَٰٓئِكَ هُمُ ٱلْمُتَّقُونَ',
     'aya_no_chakl': 'والذي جاء بالصدق وصدق به أولئك هم المتقون',
     'tafsir_aya': '( والذي جاء بالصدق وصدق به ) قال ابن عباس : " والذي جاء بالصدق " يعني رسول الله - صلى الله عليه وسلم - جاء بلا إله إلا الله " وصدق به " الرسول أيضا بلغه إلى الخلق . وقال السدي : " والذي جاء بالصدق " جبريل جاء بالقرآن ، " وصدق به " محمد - صلى الله عليه وسلم - تلقاه بالقبول . وقال الكلبي وأبو العالية : " والذي جاء بالصدق " رسول الله - صلى الله عليه وسلم - " وصدق به " أبو بك

In [12]:
query_body = {
  "size":1000,
  "query": {
    "match": {
      "tafsir_aya": {
        "query":"المتقون"
      }
    }
  }
}

In [13]:
es.search(index="quran_G2", body=query_body)

{'took': 17,
 'timed_out': False,
 '_shards': {'total': 1, 'successful': 1, 'skipped': 0, 'failed': 0},
 'hits': {'total': {'value': 10, 'relation': 'eq'},
  'max_score': 10.812934,
  'hits': [{'_index': 'quran',
    '_type': 'quran',
    '_id': 'T61TFncBarqUGLZSLgCm',
    '_score': 10.812934,
    '_source': {'aya_index_quran': 1742,
     'aya_index_sura': 35,
     'sura_name': 'سورة الرعد',
     'sura_index': 13,
     'total_verses': 43,
     'aya_chakl': 'مَّثَلُ ٱلْجَنَّةِ ٱلَّتِى وُعِدَ ٱلْمُتَّقُونَ تَجْرِى مِن تَحْتِهَا ٱلْأَنْهَٰرُ أُكُلُهَا دَآئِمٌ وَظِلُّهَا تِلْكَ عُقْبَى ٱلَّذِينَ ٱتَّقَوا۟ وَّعُقْبَى ٱلْكَٰفِرِينَ ٱلنَّارُ',
     'aya_no_chakl': 'مثل الجنة التي وعد المتقون تجري من تحتها الأنهار أكلها دائم وظلها تلك عقبى الذين اتقوا وعقبى الكافرين النار',
     'tafsir_aya': 'قوله عز وجل : ( مثل الجنة التي وعد المتقون ) أي : صفة الجنة ، كقوله تعالى : ( ولله المثل الأعلى ) ( النحل - 60 ) أي : الصفة العليا ( تجري من تحتها الأنهار ) أي : صفة الجنة التي وعد المتقون أن الأنهار تج

In [62]:

query_body = {
  "size":1000,
  "query": {
    "match": {
      "aya_no_chakl.exact": {
        "query":"أصحاب الجنة"
      }
    }
  }
}

In [63]:
es.search(index="quran2_g2", body=query_body)

{'took': 322,
 'timed_out': False,
 '_shards': {'total': 2, 'successful': 2, 'skipped': 0, 'failed': 0},
 'hits': {'total': {'value': 100, 'relation': 'eq'},
  'max_score': 16.446384,
  'hits': [{'_index': 'quran2_g2',
    '_type': '_doc',
    '_id': 'JJW7EnkBH5h4-fN0epzH',
    '_score': 16.446384,
    '_source': {'aya_index_quran': 5146,
     'aya_index_sura': 20,
     'sura_name': 'سورة الحشر',
     'sura_index': 59,
     'total_verses': 24,
     'aya_chakl': 'لَا يَسْتَوِىٓ أَصْحَٰبُ ٱلنَّارِ وَأَصْحَٰبُ ٱلْجَنَّةِ أَصْحَٰبُ ٱلْجَنَّةِ هُمُ ٱلْفَآئِزُونَ',
     'aya_no_chakl': 'لا يستوي أصحاب النار وأصحاب الجنة أصحاب الجنة هم الفائزون',
     'tafsir_aya': '"لا يستوي أصحاب النار وأصحاب الجنة أصحاب الجنة هم الفائزون".'}},
   {'_index': 'quran2_g2',
    '_type': '_doc',
    '_id': 'SZW4EnkBH5h4-fN0b5NW',
    '_score': 14.963729,
    '_source': {'aya_index_quran': 2879,
     'aya_index_sura': 24,
     'sura_name': 'سورة الفرقان',
     'sura_index': 25,
     'total_verses': 77,
     'ay

In [39]:

query_body = {
  "size":1000,
  "query": {
    "match": {
      "tafsir_aya": {
        "query":"أصحاب الجنة"
      }
    }
  }
}

In [42]:
es.search(index="quran_g2", body=query_body)

{'took': 2008,
 'timed_out': False,
 '_shards': {'total': 1, 'successful': 1, 'skipped': 0, 'failed': 0},
 'hits': {'total': {'value': 648, 'relation': 'eq'},
  'max_score': 10.906797,
  'hits': [{'_index': 'quran_g2',
    '_type': 'quran_g2',
    '_id': '9pW1EnkBH5h4-fN0c4uQ',
    '_score': 10.906797,
    '_source': {'aya_index_quran': 1004,
     'aya_index_sura': 50,
     'sura_name': 'سورة الأعراف',
     'sura_index': 7,
     'total_verses': 206,
     'aya_chakl': 'وَنَادَىٰٓ أَصْحَٰبُ ٱلنَّارِ أَصْحَٰبَ ٱلْجَنَّةِ أَنْ أَفِيضُوا۟ عَلَيْنَا مِنَ ٱلْمَآءِ أَوْ مِمَّا رَزَقَكُمُ ٱللَّهُ قَالُوٓا۟ إِنَّ ٱللَّهَ حَرَّمَهُمَا عَلَى ٱلْكَٰفِرِينَ',
     'aya_no_chakl': 'ونادى أصحاب النار أصحاب الجنة أن أفيضوا علينا من الماء أو مما رزقكم الله قالوا إن الله حرمهما على الكافرين',
     'tafsir_aya': 'قوله تعالى : ( ونادى أصحاب النار أصحاب الجنة أن أفيضوا ) أي : صبوا ، ( علينا من الماء أو مما رزقكم الله ) أي : أوسعوا علينا مما رزقكم الله من طعام الجنة .قال عطاء عن ابن عباس : لما صار أصحاب الأ

In [43]:
query_body = {
  "size":1000,
  "query": {
    "match": {
      "aya_no_chakl": {
        "query":"المؤمنون"
      }
    }
  }
}

In [46]:
es.search(index="quran_g2", body=query_body)

{'took': 86,
 'timed_out': False,
 '_shards': {'total': 1, 'successful': 1, 'skipped': 0, 'failed': 0},
 'hits': {'total': {'value': 22, 'relation': 'eq'},
  'max_score': 7.151076,
  'hits': [{'_index': 'quran_g2',
    '_type': 'quran_g2',
    '_id': '4pW5EnkBH5h4-fN0UpW3',
    '_score': 7.151076,
    '_source': {'aya_index_quran': 3544,
     'aya_index_sura': 11,
     'sura_name': 'سورة الأحزاب',
     'sura_index': 33,
     'total_verses': 73,
     'aya_chakl': 'هُنَالِكَ ٱبْتُلِىَ ٱلْمُؤْمِنُونَ وَزُلْزِلُوا۟ زِلْزَالًا شَدِيدًا',
     'aya_no_chakl': 'هنالك ابتلي المؤمنون وزلزلوا زلزالا شديدا',
     'tafsir_aya': '( هنالك ابتلي ) أي : عند ذلك اختبر المؤمنون ، بالحصر والقتال ، ليتبين المخلص من المنافق ( وزلزلوا زلزالا شديدا ) حركوا حركة شديدة .'}},
   {'_index': 'quran_g2',
    '_type': 'quran_g2',
    '_id': 'fJW4EnkBH5h4-fN0IZLs',
    '_score': 6.86644,
    '_source': {'aya_index_quran': 2674,
     'aya_index_sura': 1,
     'sura_name': 'سورة المؤمنون',
     'sura_index': 23,
     

In [82]:
query_body = {
  "size":1000,
  "query": {
    "match": {
      "tafsir_aya": {
        "query":"أبأولئك"
      }
    }
  }
}

In [83]:
es.search(index="quran2_g2", body=query_body)

{'took': 14,
 'timed_out': False,
 '_shards': {'total': 1, 'successful': 1, 'skipped': 0, 'failed': 0},
 'hits': {'total': {'value': 0, 'relation': 'eq'},
  'max_score': None,
  'hits': []}}

# Question 3

In [20]:
query_body =  {
    "query" : {
        "match_all" : {}                        
    },
    "size": 0,
    "aggs": {
    "group_by_state": {
      "terms": {
        "field": "aya_no_chakl.keyword"
      }
    }
  }
}

In [21]:
es.search(index="quran2_g2", body=query_body)

{'took': 86,
 'timed_out': False,
 '_shards': {'total': 2, 'successful': 2, 'skipped': 0, 'failed': 0},
 'hits': {'total': {'value': 6235, 'relation': 'eq'},
  'max_score': None,
  'hits': []},
 'aggregations': {'group_by_state': {'doc_count_error_upper_bound': 4,
   'sum_other_doc_count': 6144,
   'buckets': [{'key': 'فبأي آلاء ربكما تكذبان', 'doc_count': 31},
    {'key': 'ويل يومئذ للمكذبين', 'doc_count': 11},
    {'key': 'فاتقوا الله وأطيعون', 'doc_count': 8},
    {'key': 'وإن ربك لهو العزيز الرحيم', 'doc_count': 8},
    {'key': 'بسم الله الرحمن الرحيم حم', 'doc_count': 7},
    {'key': 'إن في ذلك لآية وما كان أكثرهم مؤمنين', 'doc_count': 6},
    {'key': 'بسم الله الرحمن الرحيم الم', 'doc_count': 6},
    {'key': 'ويقولون متى هذا الوعد إن كنتم صادقين', 'doc_count': 6},
    {'key': 'إلا عباد الله المخلصين', 'doc_count': 4},
    {'key': 'إنا كذلك نجزي المحسنين', 'doc_count': 4}]}}}

In [58]:
query_body = {
    "size": 0,
    "aggs" : {
        "frequent_words" : {
            "terms" : { "field" : "aya_no_chakl.stem_noshingle" }
        }
    }
}

In [59]:
es.search(index="quran2_g2", body=query_body)

{'took': 24,
 'timed_out': False,
 '_shards': {'total': 2, 'successful': 2, 'skipped': 0, 'failed': 0},
 'hits': {'total': {'value': 6235, 'relation': 'eq'},
  'max_score': None,
  'hits': []},
 'aggregations': {'frequent_words': {'doc_count_error_upper_bound': 155,
   'sum_other_doc_count': 40822,
   'buckets': [{'key': 'الله', 'doc_count': 1664},
    {'key': 'ارض', 'doc_count': 431},
    {'key': 'له', 'doc_count': 353},
    {'key': 'يوم', 'doc_count': 318},
    {'key': 'قالوا', 'doc_count': 294},
    {'key': 'قل', 'doc_count': 271},
    {'key': 'امنوا', 'doc_count': 257},
    {'key': 'كانوا', 'doc_count': 251},
    {'key': 'عذاب', 'doc_count': 248},
    {'key': 'قوم', 'doc_count': 226}]}}}

# Les découvertes ( question 4)

In [69]:
query_body = {
  "size":1000,
  "query": {
    "match": {
      "aya_no_chakl": {
        "query":"خمر"
      }
    }
  }
}

In [74]:
es.search(index="quran1_g2", body=query_body)

{'took': 22,
 'timed_out': False,
 '_shards': {'total': 2, 'successful': 2, 'skipped': 0, 'failed': 0},
 'hits': {'total': {'value': 4, 'relation': 'eq'},
  'max_score': 5.9553614,
  'hits': [{'_index': 'quran1_g2',
    '_type': '_doc',
    '_id': 'AZW1EnkBH5h4-fN0Hosc',
    '_score': 5.9553614,
    '_source': {'aya_index_quran': 759,
     'aya_index_sura': 90,
     'sura_name': 'سورة المائدة',
     'sura_index': 5,
     'total_verses': 120,
     'aya_chakl': 'يَٰٓأَيُّهَا ٱلَّذِينَ ءَامَنُوٓا۟ إِنَّمَا ٱلْخَمْرُ وَٱلْمَيْسِرُ وَٱلْأَنصَابُ وَٱلْأَزْلَٰمُ رِجْسٌ مِّنْ عَمَلِ ٱلشَّيْطَٰنِ فَٱجْتَنِبُوهُ لَعَلَّكُمْ تُفْلِحُونَ',
     'aya_no_chakl': 'يا أيها الذين آمنوا إنما الخمر والميسر والأنصاب والأزلام رجس من عمل الشيطان فاجتنبوه لعلكم تفلحون',
     'tafsir_aya': 'وله عز وجل : ( ياأيها الذين آمنوا إنما الخمر والميسر ) أي : القمار ) ( والأنصاب ) يعني : الأوثان ، سميت بذلك لأنهم كانوا ينصبونها ، واحدها نصب بفتح النون وسكون الصاد ، ونصب بضم النون مخففا ومثقلا ) ( والأزلام ) يعني : الأق

In [19]:
query_body = {
  "size":1000,
  "query": {
    "match": {
      "aya_no_chakl": {
        "query":"سكارى"
      }
    }
  }
}

In [20]:
es.search(index="quran1_G2", body=query_body)

{'took': 389,
 'timed_out': False,
 '_shards': {'total': 1, 'successful': 1, 'skipped': 0, 'failed': 0},
 'hits': {'total': {'value': 2, 'relation': 'eq'},
  'max_score': 5.5787687,
  'hits': [{'_index': 'quran1',
    '_type': '_doc',
    '_id': 'pq1WFncBarqUGLZSfAPp',
    '_score': 5.5787687,
    '_source': {'aya_index_quran': 2597,
     'aya_index_sura': 2,
     'sura_name': 'سورة الحج',
     'sura_index': 22,
     'total_verses': 78,
     'aya_chakl': 'يَوْمَ تَرَوْنَهَا تَذْهَلُ كُلُّ مُرْضِعَةٍ عَمَّآ أَرْضَعَتْ وَتَضَعُ كُلُّ ذَاتِ حَمْلٍ حَمْلَهَا وَتَرَى ٱلنَّاسَ سُكَٰرَىٰ وَمَا هُم بِسُكَٰرَىٰ وَلَٰكِنَّ عَذَابَ ٱللَّهِ شَدِيدٌ',
     'aya_no_chakl': 'يوم ترونها تذهل كل مرضعة عما أرضعت وتضع كل ذات حمل حملها وترى الناس سكارى وما هم بسكارى ولكن عذاب الله شديد',
     'tafsir_aya': '( يوم ترونها ) يعني الساعة وقيل الزلزلة ، ( تذهل ) قال ابن عباس : تشغل ، وقيل تنسى ، يقال ذهلت عن كذا أي تركته واشتغلت بغيره . ( كل مرضعة عما أرضعت ) أي كل امرأة معها ولد ترضعه يقال امرأة مرضع بلا هاء

In [77]:
query_body = {
  "size":1000,
  "query": {
    "match": {
      "aya_no_chakl": {
        "query":"إعصار فيه نار"
      }
    }
  }
}


In [79]:
es.search(index="quran2_g2", body=query_body)

{'took': 314,
 'timed_out': False,
 '_shards': {'total': 1, 'successful': 1, 'skipped': 0, 'failed': 0},
 'hits': {'total': {'value': 123, 'relation': 'eq'},
  'max_score': 21.520477,
  'hits': [{'_index': 'quran2_g2',
    '_type': '_doc',
    '_id': 'HJW0EnkBH5h4-fN0gIlh',
    '_score': 21.520477,
    '_source': {'aya_index_quran': 273,
     'aya_index_sura': 266,
     'sura_name': 'سورة البقرة',
     'sura_index': 2,
     'total_verses': 286,
     'aya_chakl': 'أَيَوَدُّ أَحَدُكُمْ أَن تَكُونَ لَهُۥ جَنَّةٌ مِّن نَّخِيلٍ وَأَعْنَابٍ تَجْرِى مِن تَحْتِهَا ٱلْأَنْهَٰرُ لَهُۥ فِيهَا مِن كُلِّ ٱلثَّمَرَٰتِ وَأَصَابَهُ ٱلْكِبَرُ وَلَهُۥ ذُرِّيَّةٌ ضُعَفَآءُ فَأَصَابَهَآ إِعْصَارٌ فِيهِ نَارٌ فَٱحْتَرَقَتْ كَذَٰلِكَ يُبَيِّنُ ٱللَّهُ لَكُمُ ٱلْءَايَٰتِ لَعَلَّكُمْ تَتَفَكَّرُونَ',
     'aya_no_chakl': 'أيود أحدكم أن تكون له جنة من نخيل وأعناب تجري من تحتها الأنهار له فيها من كل الثمرات وأصابه الكبر وله ذرية ضعفاء فأصابها إعصار فيه نار فاحترقت كذلك يبين الله لكم الآيات لعلكم تتفكرون',
   

# Itération 3

# Complex query 1

In [18]:
query_body = {
  "query": {
    "bool": {
      "must": [{
        "query_string": {
            "query" :"aya_no_chakl:' (جنة AND نار)'"
        },
        "query_string": {
            "query" :"aya_no_chakl:' (كافرون OR مؤمنون)'"
        }
      }]
    }
  }
}



In [19]:
es.search(index="quran1_G2", body=query_body)

{'took': 213,
 'timed_out': False,
 '_shards': {'total': 1, 'successful': 1, 'skipped': 0, 'failed': 0},
 'hits': {'total': {'value': 315, 'relation': 'eq'},
  'max_score': 9.3648815,
  'hits': [{'_index': 'quran1',
    '_type': '_doc',
    '_id': 'h6xRFncBarqUGLZSD_37',
    '_score': 9.3648815,
    '_source': {'aya_index_quran': 1030,
     'aya_index_sura': 76,
     'sura_name': 'سورة الأعراف',
     'sura_index': 7,
     'total_verses': 206,
     'aya_chakl': 'قَالَ ٱلَّذِينَ ٱسْتَكْبَرُوٓا۟ إِنَّا بِٱلَّذِىٓ ءَامَنتُم بِهِۦ كَٰفِرُونَ',
     'aya_no_chakl': 'قال الذين استكبروا إنا بالذي آمنتم به كافرون',
     'tafsir_aya': '( قال الذين استكبروا إنا بالذي آمنتم به كافرون ) جاحدون .'}},
   {'_index': 'quran1',
    '_type': '_doc',
    '_id': 'VaxSFncBarqUGLZSdP8z',
    '_score': 9.067297,
    '_source': {'aya_index_quran': 1492,
     'aya_index_sura': 19,
     'sura_name': 'سورة هود',
     'sura_index': 11,
     'total_verses': 123,
     'aya_chakl': 'ٱلَّذِينَ يَصُدُّونَ عَن سَبِيلِ ٱ

# Complex query 2

In [38]:

query_body = {

 "query": {
    "bool": {
      "must": [
        {
        "match": {
                  "sura_name": {"query": "سورة آل عمران",
                                "operator": "and"}
                  
                }
        },
          
        {
          "match": {
                  "aya_no_chakl": {"query": "آمنا",
                                "operator": "and"}
                  
                }
            },
            {
                "match": {
                  "aya_no_chakl": {"query": "مسلمون",
                                "operator": "and"}
                  
                }
              },
          {
                "match": {
                  "aya_no_chakl": {"query": "النبيون",
                                "operator": "and"}
                  
                }
              }


      ]
    }
  }
}

In [39]:
es.search(index="quran1_G2", body=query_body)

{'took': 5,
 'timed_out': False,
 '_shards': {'total': 1, 'successful': 1, 'skipped': 0, 'failed': 0},
 'hits': {'total': {'value': 1, 'relation': 'eq'},
  'max_score': 15.681565,
  'hits': [{'_index': 'quran1',
    '_type': '_doc',
    '_id': '-6xPFncBarqUGLZSN_oI',
    '_score': 15.681565,
    '_source': {'aya_index_quran': 377,
     'aya_index_sura': 84,
     'sura_name': 'سورة آل عمران',
     'sura_index': 3,
     'total_verses': 200,
     'aya_chakl': 'قُلْ ءَامَنَّا بِٱللَّهِ وَمَآ أُنزِلَ عَلَيْنَا وَمَآ أُنزِلَ عَلَىٰٓ إِبْرَٰهِيمَ وَإِسْمَٰعِيلَ وَإِسْحَٰقَ وَيَعْقُوبَ وَٱلْأَسْبَاطِ وَمَآ أُوتِىَ مُوسَىٰ وَعِيسَىٰ وَٱلنَّبِيُّونَ مِن رَّبِّهِمْ لَا نُفَرِّقُ بَيْنَ أَحَدٍ مِّنْهُمْ وَنَحْنُ لَهُۥ مُسْلِمُونَ',
     'aya_no_chakl': 'قل آمنا بالله وما أنزل علينا وما أنزل على إبراهيم وإسماعيل وإسحاق ويعقوب والأسباط وما أوتي موسى وعيسى والنبيون من ربهم لا نفرق بين أحد منهم ونحن له مسلمون',
     'tafsir_aya': 'قوله تعالى : ( قل آمنا بالله وما أنزل علينا وما أنزل على إبراهيم وإس

# Complex query 3

In [34]:
query_body = {

 "query": {
    "bool": {
      "must": [
          
        
            {
                "match": {
                  "aya_no_chakl": {"query": "عين"}
                  
                }
              },
          {
                "match": {
                  "aya_no_chakl": {"query": "جن"}
                  
                }
              }


      ]
    }
  },
  "fields": ["sura_name", "aya_chakl"],
  "_source": "false"
}

In [35]:
es.search(index="quran1_G2", body=query_body)

{'took': 2,
 'timed_out': False,
 '_shards': {'total': 1, 'successful': 1, 'skipped': 0, 'failed': 0},
 'hits': {'total': {'value': 1, 'relation': 'eq'},
  'max_score': 6.5362473,
  'hits': [{'_index': 'quran1',
    '_type': '_doc',
    '_id': 'o61ZFncBarqUGLZSdQdl',
    '_score': 6.5362473,
    '_source': {},
    'fields': {'sura_name': ['سورة سبإ'],
     'aya_chakl': ['وَلِسُلَيْمَٰنَ ٱلرِّيحَ غُدُوُّهَا شَهْرٌ وَرَوَاحُهَا شَهْرٌ وَأَسَلْنَا لَهُۥ عَيْنَ ٱلْقِطْرِ وَمِنَ ٱلْجِنِّ مَن يَعْمَلُ بَيْنَ يَدَيْهِ بِإِذْنِ رَبِّهِۦ وَمَن يَزِغْ مِنْهُمْ عَنْ أَمْرِنَا نُذِقْهُ مِنْ عَذَابِ ٱلسَّعِيرِ']}}]}}

# Complex query 4

In [50]:
query_body = { 
"query": {
    "bool": {
      "must": [
          
        
            {
                "match": {
                  "sura_index": {"query": "41"}
                  
                }
              },
          {
                "range": {
                    "aya_index_sura": {
                            "gte": 30,
                            "lte": 31
                                  }
                          }
              },
          
          {"bool": {
              "filter": [
                { "term": { "aya_no_chakl": "ربنا"   }}
                          ]
                  }
          }

      ]
    }
  }
}

In [51]:
es.search(index="quran1_G2", body=query_body)

{'took': 228,
 'timed_out': False,
 '_shards': {'total': 1, 'successful': 1, 'skipped': 0, 'failed': 0},
 'hits': {'total': {'value': 1, 'relation': 'eq'},
  'max_score': 2.0,
  'hits': [{'_index': 'quran1',
    '_type': '_doc',
    '_id': 'Ga1bFncBarqUGLZSQwq-',
    '_score': 2.0,
    '_source': {'aya_index_quran': 4248,
     'aya_index_sura': 30,
     'sura_name': 'سورة فصلت',
     'sura_index': 41,
     'total_verses': 54,
     'aya_chakl': 'إِنَّ ٱلَّذِينَ قَالُوا۟ رَبُّنَا ٱللَّهُ ثُمَّ ٱسْتَقَٰمُوا۟ تَتَنَزَّلُ عَلَيْهِمُ ٱلْمَلَٰٓئِكَةُ أَلَّا تَخَافُوا۟ وَلَا تَحْزَنُوا۟ وَأَبْشِرُوا۟ بِٱلْجَنَّةِ ٱلَّتِى كُنتُمْ تُوعَدُونَ',
     'aya_no_chakl': 'إن الذين قالوا ربنا الله ثم استقاموا تتنزل عليهم الملائكة ألا تخافوا ولا تحزنوا وأبشروا بالجنة التي كنتم توعدون',
     'tafsir_aya': 'قوله عز وجل : ( إن الذين قالوا ربنا الله ثم استقاموا ) سئل أبو بكر الصديق - رضي الله تعالى عنه - عن الاستقامة فقال : أن لا تشرك بالله شيئا . وقال عمر بن الخطاب - رضي الله عنه - : " الاستقامة " أن تستقيم

# Complex query 5

In [108]:
query_body = {

 "query": {
    "bool": {
      "should": [
          
        
        {
                "match": {
                  "aya_no_chakl": {"query": "موسى + بقرة",
                                "operator": "or"}
                  
                }
        },
        {
                "match": {
                  "aya_no_chakl": {"query": "الغراب + ادم",
                                "operator": "or"}
                  
                }
        },
        {
                "match": {
                  "aya_no_chakl": {"query": "هدهد + سليمان",
                                "operator": "or"}
                  
                }
        },
        {
                "match": {
                  "aya_no_chakl": {"query": "يوسف + الذئب",
                                "operator": "or"}
                  
                }
        },
        {
                "match": {
                  "aya_no_chakl": {"query": "داوود + نعجة",
                                "operator": "or"}
                  
                }
        }
      ]
  }
}
}

In [109]:
es.search(index="quran1_G2", body=query_body)

{'took': 47,
 'timed_out': False,
 '_shards': {'total': 1, 'successful': 1, 'skipped': 0, 'failed': 0},
 'hits': {'total': {'value': 205, 'relation': 'eq'},
  'max_score': 16.358358,
  'hits': [{'_index': 'quran1',
    '_type': '_doc',
    '_id': '6qxQFncBarqUGLZSmfyT',
    '_score': 16.358358,
    '_source': {'aya_index_quran': 873,
     'aya_index_sura': 84,
     'sura_name': 'سورة الأنعام',
     'sura_index': 6,
     'total_verses': 165,
     'aya_chakl': 'وَوَهَبْنَا لَهُۥٓ إِسْحَٰقَ وَيَعْقُوبَ كُلًّا هَدَيْنَا وَنُوحًا هَدَيْنَا مِن قَبْلُ وَمِن ذُرِّيَّتِهِۦ دَاوُۥدَ وَسُلَيْمَٰنَ وَأَيُّوبَ وَيُوسُفَ وَمُوسَىٰ وَهَٰرُونَ وَكَذَٰلِكَ نَجْزِى ٱلْمُحْسِنِينَ',
     'aya_no_chakl': 'ووهبنا له إسحاق ويعقوب كلا هدينا ونوحا هدينا من قبل ومن ذريته داوود وسليمان وأيوب ويوسف وموسى وهارون وكذلك نجزي المحسنين',
     'tafsir_aya': '( ووهبنا له إسحاق ويعقوب كلا هدينا ) وفقنا وأرشدنا . ( ونوحا هدينا من قبل ) أي : من قبل إبراهيم ، ( ومن ذريته ) أي ومن ذرية نوح عليه السلام ، ولم يرد من ذرية إبر

# Complex query 6

In [110]:
query_body = {

 "query": {
    "bool": {
      "should": [
          
        
        {
                "match": {
                  "aya_no_chakl": {"query": "خالدين + نار",
                                "operator": "or"}
                  
                }
        },
        {
                "match": {
                  "aya_no_chakl": {"query": "خالدين + جنة",
                                "operator": "or"}
                  
                }
        }
      ]
  }
}
}

In [111]:
es.search(index="quran1_G2", body=query_body)

{'took': 500,
 'timed_out': False,
 '_shards': {'total': 1, 'successful': 1, 'skipped': 0, 'failed': 0},
 'hits': {'total': {'value': 302, 'relation': 'eq'},
  'max_score': 13.789851,
  'hits': [{'_index': 'quran1',
    '_type': '_doc',
    '_id': 'mK1dFncBarqUGLZS5w35',
    '_score': 13.789851,
    '_source': {'aya_index_quran': 5143,
     'aya_index_sura': 17,
     'sura_name': 'سورة الحشر',
     'sura_index': 59,
     'total_verses': 24,
     'aya_chakl': 'فَكَانَ عَٰقِبَتَهُمَآ أَنَّهُمَا فِى ٱلنَّارِ خَٰلِدَيْنِ فِيهَا وَذَٰلِكَ جَزَٰٓؤُا۟ ٱلظَّٰلِمِينَ',
     'aya_no_chakl': 'فكان عاقبتهما أنهما في النار خالدين فيها وذلك جزاء الظالمين',
     'tafsir_aya': 'يقول الله تعالى ( فكان عاقبتهما ) يعني الشيطان وذلك الإنسان ( أنهما في النار خالدين فيها وذلك جزاء الظالمين ) قال ابن عباس : ضرب الله هذا المثل ليهود بني النضير والمنافقين من أهل المدينة وذلك أن الله - عز وجل - أمر نبيه - صلى الله عليه وسلم - بإجلاء بني النضير عن المدينة فدس المنافقون إليهم وقالوا : لا تجيبوا محمدا إلى ما دعاك

# Complex query 7

In [152]:
L = ["الله "," الرحمن "," الرحيم "," الملك "," القدوس "," السلام "," المؤمن "," المهيمن "," العزيز "," الجبار "," المتكبر "," الخالق "," البارئ "," المصور "," الغفار "," القهار "," الوهاب "," الرزاق "," الفتاح "," العليم "," القابض "," الباسط "," الخافض "," الرافع "," المعز "," المذل "," السميع "," البصير "," الحكم "," العدل "," اللطيف "," الخبير "," الحليم "," العظيم "," الغفور "," الشكور "," العلي "," الكبير "," الحفيظ "," المقيت "," الحسيب "," الجليل "," الكريم "," الرقيب "," المجيب "," الواسع "," الحكيم "," الودود "," المجيد "," الباعث "," الشهيد "," الحق "," الوكيل "," القوي "," المتين "," الولي "," الحميد "," المحصي "," المبدئ "," المعيد","المحيي"," المميت "," الحي "," القيوم "," الواجد "," الماجد "," الواحد "," الأحد "," الصمد "," القادر "," المقتدر "," المقدم "," المؤخر "," الأول "," الآخر "," الظاهر "," الباطن "," الوالي "," المتعالي "," البر "," التواب "," المنتقم "," العفو "," الرءوف "," مالك "," ذو الجلال والإكرام "," المقسط "," الجامع ","الغني "," المغني "," المانع "," الضار "," النافع "," النور "," الهادي "," البديع "," الباقي","الوارث "," الرشيد "," الصبور"]

In [150]:
query_body = {

 "query": {
    "bool": {
      "must": [
          
        
        {
                "match": {
                  "aya_no_chakl": {"query": "رحمن  OR لرحيم  ORالملك  OR لقدوس  OR لسلام  OR لمؤمن  OR مهيمن  OR لعزيز  OR لجبار  OR متكبر OR لخالق  OR لبارئ  OR لمصور  OR لغفار  OR لقهار  OR لوهاب  OR لرزاق  OR لفتاح  OR لعليم  OR لقابض  OR لباسط  OR لخافض  OR لرافع  ORالمعز  ORالمذل  OR لسميع  OR لبصير  ORالحكم  ORالعدل  OR للطيف  OR لخبير  OR لحليم  OR لعظيم  OR لغفور  OR لشكور  ORالعلي  OR لكبير  OR لحفيظ  OR لمقيت  OR لحسيب  OR لجليل  OR لكريم  OR لرقيب  OR لمجيب  OR لواسع  OR لحكيم  OR لودود  OR لمجيد  OR لباعث  OR لشهيد  AN الحق  OR لوكيل  OR القوي  OR لمتين  ORالولي  OR لحميد  OR لمحصي  OR لمبدئ  OR المعيد OR المحيي OR لمميت  AN الحي  OR لقيوم  OR لواجد  OR لماجد  OR لواحد  OR الأحد   OR الصمد  OR لقادر  OR مقتدر  OR لمقدم  OR لمؤخر  ORالأول  ORالآخر  OR لظاهر  OR لباطن  OR لوالي  OR تعالي  AN البر  OR لتواب  OR منتقم  OR العفو  OR لرءوف  AN مالك  OR ذو الجلال إكرام  OR لمقسط  OR لجامع  OR الغني  OR لمغني  OR لمانع  ORالضار  OR لنافع  ORالنور  OR لهادي  OR لبديع  OR الباقي OR لوارث  OR لرشيد  OR الصبور"}
                  
                }
        }
      ]
  }
}
}

In [151]:
es.search(index="quran1_G2", body=query_body)

{'took': 7,
 'timed_out': False,
 '_shards': {'total': 1, 'successful': 1, 'skipped': 0, 'failed': 0},
 'hits': {'total': {'value': 615, 'relation': 'eq'},
  'max_score': 24.870918,
  'hits': [{'_index': 'quran1',
    '_type': '_doc',
    '_id': 'wa1dFncBarqUGLZSLgyA',
    '_score': 24.870918,
    '_source': {'aya_index_quran': 4928,
     'aya_index_sura': 27,
     'sura_name': 'سورة الرحمن',
     'sura_index': 55,
     'total_verses': 78,
     'aya_chakl': 'وَيَبْقَىٰ وَجْهُ رَبِّكَ ذُو ٱلْجَلَٰلِ وَٱلْإِكْرَامِ',
     'aya_no_chakl': 'ويبقى وجه ربك ذو الجلال والإكرام',
     'tafsir_aya': '" ويبقى وجه ربك ذو الجلال "، ذو العظمة والكبرياء، " والإكرام "، مكرم أنبيائه وأوليائه بلطفه مع جلاله وعظمته.'}},
   {'_index': 'quran1',
    '_type': '_doc',
    '_id': '9K1dFncBarqUGLZSVgy8',
    '_score': 18.467854,
    '_source': {'aya_index_quran': 4979,
     'aya_index_sura': 78,
     'sura_name': 'سورة الرحمن',
     'sura_index': 55,
     'total_verses': 78,
     'aya_chakl': 'تَبَٰرَكَ ٱسْمُ 

# Complex query 8

In [75]:
query_body = {

 "query": {
    "bool": {
      "must": [
          
        
        {
                "match": {
                  "aya_no_chakl": {"query": "الإنجيل  OR التوراة  OR زبور"}
                  
                }
        }
      ]
  }
}
}

In [78]:
es.search(index="quran1_g2", body=query_body)

{'took': 245,
 'timed_out': False,
 '_shards': {'total': 2, 'successful': 2, 'skipped': 0, 'failed': 0},
 'hits': {'total': {'value': 19, 'relation': 'eq'},
  'max_score': 15.696913,
  'hits': [{'_index': 'quran1_g2',
    '_type': '_doc',
    '_id': 'YJW0EnkBH5h4-fN0lImn',
    '_score': 15.696913,
    '_source': {'aya_index_quran': 341,
     'aya_index_sura': 48,
     'sura_name': 'سورة آل عمران',
     'sura_index': 3,
     'total_verses': 200,
     'aya_chakl': 'وَيُعَلِّمُهُ ٱلْكِتَٰبَ وَٱلْحِكْمَةَ وَٱلتَّوْرَىٰةَ وَٱلْإِنجِيلَ',
     'aya_no_chakl': 'ويعلمه الكتاب والحكمة والتوراة والإنجيل',
     'tafsir_aya': 'قوله تعالى : ( ويعلمه الكتاب ) قرأ أهل المدينة وعاصم ويعقوب بالياء لقوله تعالى : ( كذلك الله يخلق ما يشاء ) وقيل : رده على قوله : ( إن الله يبشرك ) ( ويعلمه ) وقرأ الآخرون بالنون على التعظيم كقوله تعالى : ( ذلك من أنباء الغيب نوحيه إليك ) قوله : ( الكتاب ) أي الكتابة والخط ( والحكمة ) العلم والفقه ( والتوراة والإنجيل ) علمه الله التوراة والإنجيل'}},
   {'_index': 'quran1_g2'